In [ ]:
# LAST USE: 2025-09-23 11:15 

In [61]:
import numpy as np
import pandas as pd
import sqlite3
from datetime import datetime
import re
import sys
import base64
import json

def correct_coding(text):
    if not isinstance(text, str):
        return text
    if 'Ã¤' in text or 'Ã¶' in text or 'Ã¼' in text or 'ÃŸ' in text or \
       'Ã„' in text or 'Ã–' in text or 'Ã' in text or 'Ãœ' in text: 
        return text.encode('latin1').decode('utf-8')
    else:
        return text
    
def build_query_str(fg, fcid, fid, fcont, muid, usergroup):
    # mts = datetime.now().strftime("%Y-%m-%d %H:%M:%S")
    mts = "2025-08-18 23:59:59"
    query = "INSERT OR IGNORE INTO forms_" + str(fg) + "(fcid,muid,fid,fcont,usergroup,mts) VALUES (" + str(fcid) + "," + str(muid) + "," + str(fid) + ",'" + str(fcont)  + "','" + str(usergroup) + "','" + mts + "')"
    return query
        
def get_one_val_from_cedur(table, val, pid):
    cursor_src.execute("SELECT " + val + " FROM " + table + " WHERE pid='" + pid +  "'")
    r = cursor_src.fetchone()
    return r[0] if r else "-"

def get_rows_from_cedur(table, pid):
    cursor_src.execute("SELECT * FROM " + table + " WHERE pid='" + pid +  "'")
    rows = cursor_src.fetchall()
    return rows if rows else []
               
def get_visite_fcid():
    cursor_src.execute("SELECT cid, fcid FROM CEDUR3_Info")
    rows = cursor_src.fetchall()
    fcid_a = {}
    for cid, fcid in rows:
        fcid_a[cid] = fcid
    return fcid_a

def import_patient_base(praxis_a, check_if_fcid_exists, num_to_import = 0):
    fg = 10003
    # print("Clean!")
    cursor_src.execute("SELECT *,MIN(createdAt) AS first_createdAt FROM CEDUR3_patient WHERE " + praxis_a['where_str'] + " GROUP BY pid")
    # rows = cursor.fetchall()
    # cursor.fetchone() 
    # cursor.fetchmany(10)  
    if (num_to_import):
        rows = cursor_src.fetchmany(num_to_import)  
    else:
        rows = cursor_src.fetchall()
    results_as_dicts = [dict(row) for row in rows]
    # print(results_as_dicts)
    i = 0
    if results_as_dicts:
        for row_dict in results_as_dicts:
            if i % 100 == 0: 
                print(str(i) + " ", end="", flush=True)
            createdAt = row_dict['first_createdAt']
            dt_obj = datetime.strptime(createdAt[:23], '%Y-%m-%dT%H:%M:%S.%f')
            fcid = str(dt_obj.strftime('%Y%m%d%H%M%S')) + '00'
            fcid = int(fcid)
            # print(fcid)
            while fcid in check_if_fcid_exists:
                print(f"{fcid} schon vorhanden, erhöhe um 1")
                fcid += 1
            check_if_fcid_exists[fcid] = True
            # print(row_dict) und # row_dict['name']) 
            # for column_name, value in row_dict.items():
            #     print(f"  {column_name}: {value}")
            gender = ""
            if row_dict['gender'] == 'male':
                gender = 'männlich';
            if row_dict['gender'] == 'female':
                gender = 'weiblich';
            # fg, fcid, fid, fcont, muid, usergroup, mts):
            query = build_query_str(fg, fcid, 10, praxis_a['muid'], praxis_a['muid'], praxis_a['usergroup'])
            cursor.execute(query)
            query = build_query_str(fg, fcid, 20, praxis_a['usergroup'], praxis_a['muid'], praxis_a['usergroup'])
            cursor.execute(query)
            query = build_query_str(fg, fcid, 91, row_dict['externalId'], praxis_a['muid'], praxis_a['usergroup'])
            cursor.execute(query)
            query = build_query_str(fg, fcid, 92, row_dict['number'], praxis_a['muid'], praxis_a['usergroup'])
            cursor.execute(query)
            query = build_query_str(fg, fcid, 10003020, row_dict['yearOfBirth'], praxis_a['muid'], praxis_a['usergroup'])
            cursor.execute(query)
            query = build_query_str(fg, fcid, 96, gender, praxis_a['muid'], praxis_a['usergroup'])
            cursor.execute(query)
            query = build_query_str(fg, fcid, 101, row_dict['createdAt'], praxis_a['muid'], praxis_a['usergroup'])
            cursor.execute(query)
            query = build_query_str(fg, fcid, 102, row_dict['pid'], praxis_a['muid'], praxis_a['usergroup'])
            cursor.execute(query)
            # conn.commit()
            diagnosis = get_one_val_from_cedur('CEDUR3_allgemein', 'CDAI001', row_dict['pid'])
            query = build_query_str(fg, fcid, 95, diagnosis, praxis_a['muid'], praxis_a['usergroup'])
            cursor.execute(query)
            # conn.commit()
            size = get_one_val_from_cedur('CEDUR3_allgemein', 'CDAI_Size', row_dict['pid'])
            query = build_query_str(fg, fcid, 97, size, praxis_a['muid'], praxis_a['usergroup'])
            cursor.execute(query)
            # conn.commit()
            # diagnosis = get_one_val_from_cedur('CEDUR3_allgemein', 'CDAI_Size', row_dict['pid'])
            # query = build_query_str(fg, fcid, 97, diagnosis, praxis_a['muid'], praxis_a['usergroup'])
            # cursor.execute(query)
            # conn.commit()
            cursor.execute("UPDATE forms_10003 SET fcont = REPLACE(fcont, ' cm', '') WHERE fid=97");
            conn.commit()
            fcid = fcid + 1
            i = i + 1
            #print("-" * 20)

def get_cedur2miq_a(cedur2miq_a, fg, table_prefix):
    cursor.execute("SELECT * FROM forms_definition WHERE fg = " + str(fg))
    rows = cursor.fetchall()
    results_as_dicts = [dict(row) for row in rows]
    
    for row_dict in results_as_dicts:
        fname_string = row_dict['fname']
        match = re.search(r'\[(.*?)\]', fname_string)
        if match:
            extrahiert_string = match.group(1)
            if (extrahiert_string.split('.')[1] == table_prefix):
                column_name = extrahiert_string.split('.')[2]
                # print(f" {row_dict['fid']} : {column_name}") 
                cedur2miq_a[column_name] = row_dict['fid']
    cedur2miq_a['CDAI001'] = 95 
    return cedur2miq_a

def clean_replace(column_id, conform_replace,text_value):
    if not isinstance(text_value, str):
        return text_value
    text_value = correct_coding(text_value)
    zu_ersetzender_string = conform_replace.get(column_id)
    if zu_ersetzender_string:
        return text_value.replace(zu_ersetzender_string, '')
    return text_value

def get_patient_list_a(praxis_a):
    patient_fcid_a = []
    cursor.execute("SELECT DISTINCT fcid FROM forms_10003 WHERE usergroup = "+ str(praxis_a['usergroup']) + " and fcid<= " + str(praxis_a['fcid_import_border']) + " ORDER BY fcid")
    rows = cursor.fetchall()
    results_as_dicts = [dict(row) for row in rows]
    for row_dict in results_as_dicts:
        patient_fcid_a.append(row_dict['fcid'])
    return patient_fcid_a

def get_patient_data(patient_fcid):
    cursor.execute("SELECT * FROM forms_10003 WHERE fid<>97 and fid<>101 and fid<>10003020 and fcid = " + str(patient_fcid) )
    rows = cursor.fetchall()
    patient_a = {}
    results_as_dicts = [dict(row) for row in rows]
    if results_as_dicts:
        for row_dict in results_as_dicts:
            patient_a[row_dict['fid']] = row_dict['fcont']  
        patient_a[90] = patient_fcid
    return patient_a

def add_patient_base_data(fg, fcid, patient_a):
    query = build_query_str(fg, fcid, 10, patient_a[10], patient_a[10], patient_a[20])
    cursor.execute(query)
    query = build_query_str(fg, fcid, 20, patient_a[20], patient_a[10], patient_a[20])
    cursor.execute(query)
    query = build_query_str(fg, fcid, 90, patient_a[90], patient_a[10], patient_a[20])
    cursor.execute(query)
    query = build_query_str(fg, fcid, 91, patient_a[91], patient_a[10], patient_a[20])
    cursor.execute(query)
    query = build_query_str(fg, fcid, 92, patient_a[92], patient_a[10], patient_a[20])
    cursor.execute(query)
    query = build_query_str(fg, fcid, 93, patient_a[93], patient_a[10], patient_a[20])
    cursor.execute(query)
    query = build_query_str(fg, fcid, 94, patient_a[94], patient_a[10], patient_a[20])
    cursor.execute(query)
    query = build_query_str(fg, fcid, 95, patient_a[95], patient_a[10], patient_a[20])
    cursor.execute(query)
    query = build_query_str(fg, fcid, 96, patient_a[96], patient_a[10], patient_a[20])
    cursor.execute(query)
    query = build_query_str(fg, fcid, 97, patient_a[97], patient_a[10], patient_a[20])
    cursor.execute(query)
    conn.commit()

def format_date(date_str: str) -> str:
    if not date_str or not isinstance(date_str, str):
        return ""
    parts = date_str.split("-")
    if len(parts) == 3: 
        year, month, day = parts
        return f"{day.zfill(2)}.{month.zfill(2)}.{year}"
    elif len(parts) == 2:
        year, month = parts
        return f"{month.zfill(2)}.{year}"
    elif len(parts) == 1: 
        return parts[0]
    else:
        raise ValueError(f"Ungültiges Datumsformat: {date_str}")

def compare_dicts(new_dict, live_dict):
    only_in_new = {k: new_dict[k] for k in new_dict if k not in live_dict}
    only_in_live = {k: live_dict[k] for k in live_dict if k not in new_dict}
    changed = {k: (live_dict[k], new_dict[k]) 
               for k in new_dict 
               if k in live_dict and new_dict[k] != live_dict[k]}
    unchanged = {k: new_dict[k] 
                 for k in new_dict 
                 if k in live_dict and new_dict[k] == live_dict[k]}

    return {
        "only_in_new": only_in_new,
        "only_in live_dict": only_in_live,
        "changed": changed,
        "unchanged": unchanged
    }

def get_patient_fcid(field):
    # 102 = pid
    # 92 = Praxis-Kuerzel
    cursor.execute("SELECT fcid,fcont as pid FROM forms_10003 WHERE fid=" + str(field))
    rows = cursor.fetchall()
    fcid_a = {}
    for fcid, pid in rows:
        fcid_a[fcid] = pid
    return fcid_a

def simulate_patient_import_fcid(field):
    # pid, number
    cursor_src.execute("SELECT *,MIN(createdAt) AS first_createdAt FROM CEDUR3_patient WHERE SUBSTR(number, 1, 2) = 'HW' OR SUBSTR(number, 1, 5) = 'G6303' GROUP BY pid")
    rows = cursor_src.fetchall()
    results_as_dicts = [dict(row) for row in rows]
    patient_fcid_new_a = {}
    if results_as_dicts:
        for row_dict in results_as_dicts:
            createdAt = row_dict['first_createdAt']
            dt_obj = datetime.strptime(createdAt[:23], '%Y-%m-%dT%H:%M:%S.%f')
            fcid = str(dt_obj.strftime('%Y%m%d%H%M%S')) + '00'
            fcid = int(fcid)
            patient_fcid_new_a[fcid] = row_dict[field]
    return patient_fcid_new_a

db_source = r'C:\xampp\htdocs\MIQ_projects\cedur\db\cedur_3.sqlite3'
db_target = r'C:\xampp\htdocs\MIQ_projects\cedur\db\cedur.sqlite3'
# db_source = r'C:\xampp\htdocs\cedur\py\cedur3.sqlite3'
# db_target = r'C:\xampp\htdocs\cedur\py\cedur.sqlite3'

# db_path = r'C:\xampp\htdocs\cedur\py\cedur.sqlite3'

conn_source = sqlite3.connect(db_source)
conn_source.row_factory = sqlite3.Row 
cursor_src = conn_source.cursor()

conn = sqlite3.connect(db_target)
conn.row_factory = sqlite3.Row 
cursor = conn.cursor()

# CHECK!!!!
# conn_source.execute("UPDATE CEDUR3_Info SET cleaned_created = ( SELECT SUBSTR( REPLACE(T2.createdAt, 'T', ' '), 1, INSTR(REPLACE(T2.createdAt, 'T', ' '), '.') - 1 ) FROM CEDUR3_patient AS T2 WHERE T2.cid = CEDUR3_Info.cid );")
# conn_source.execute("UPDATE CEDUR3_Info SET cleaned_visit = SUBSTR( REPLACE(Befragungerstelltam, 'T', ' '), 1, INSTR(REPLACE(Befragungerstelltam, 'T', ' '), '.') - 1 );")
# conn_source.execute("UPDATE CEDUR3_Info SET fcid = strftime('%Y%m%d00', cleaned_visit) || cid;")

In [62]:
# CHECK IF UPDATE IMPORT SAME User

# patient_fcid_live_a = get_patient_fcid(92)
# patient_fcid_new_a = simulate_patient_import_fcid('number')

# patient_fcid_live_a = get_patient_fcid(102)
# patient_fcid_new_a = simulate_patient_import_fcid('pid')

# compare_dicts(patient_fcid_new_a, patient_fcid_live_a)

In [63]:
# DELETE FROM `forms_1`;
# DELETE FROM `forms_10000`;
# DELETE FROM `forms_10003`;
# DELETE FROM `forms_10005`;
# DELETE FROM `forms_10010`;
# DELETE FROM `forms_10020`;
# DELETE FROM `forms_10050`;
# DELETE FROM `forms_99901`;
# DELETE FROM `forms_99902`;
# DELETE FROM `forms_definition`;
# DELETE FROM `token_store`;
# DELETE FROM `user_miq`;
# DELETE FROM `user_miq_log`;
# forms_definition einspielen


In [64]:
# CEDUR cols to FID
cedur2miq_a = {}
cedur2miq_a = get_cedur2miq_a(cedur2miq_a, 10010, 'Allgemein')
cedur2miq_a = get_cedur2miq_a(cedur2miq_a, 10010, 'lebensqualitaet')
cedur2miq_a

{'Montreal_Lokalisation_CU': 102000,
 'DatumErstdiagnose': 102200,
 'DatumErsteSymptome': 102300,
 'CDAI003': 102400,
 'CDAI003Tage': 102500,
 'CDAI_Size': 102600,
 'CDAI006': 102700,
 'Raucher': 102800,
 'menge_ezig': 103000,
 'mengepfeif': 103100,
 'menge_tabaker': 103200,
 'menge_zigar': 103300,
 'menge_zigarette': 103400,
 'CDAI009': 103500,
 'CDAI014': 103600,
 'mayo_pga': 103700,
 'mayo_endo': 103800,
 'CDAI010': 103900,
 'CDAI011': 104000,
 'CDAI012': 104200,
 'fistelact': 104300,
 'fist_and': 104400,
 'CDAI012_hatten': 104500,
 'Stenosen': 104800,
 'stenose_ort': 104910,
 'Verwandte': 105000,
 'Verwandte_MutterVater': 105100,
 'Verwandte_BruderSchwester': 105200,
 'zwilling': 105300,
 'Verwandte_SohnTochter': 105400,
 'Verwandte_GrossvaterGrossmutter': 105500,
 'Verwandte_TanteOnkel': 105600,
 'Verwandte_NeffeNichte': 105700,
 'Verwandte_CousinCousine': 105800,
 'Verwandte_Andere': 105900,
 'taetigkeit': 106000,
 'berentedErkrankung': 106100,
 'CDAI002': 106200,
 'Fehltage': 10

In [65]:
# # Some muid-corrections
# cursor.execute("UPDATE forms_10003 SET muid=-1 WHERE muid=-9;")
# cursor.execute("UPDATE forms_10005 SET muid=-1 WHERE muid=-9;")
# cursor.execute("UPDATE forms_10010 SET muid=-1 WHERE muid=-9;")
# conn.commit()

In [ ]:

# Get VISITE cid to FCID (from info Table => cid+clean_created)
fcid_a = get_visite_fcid()

praxis_a = {
    'Howaldt': {
        'name': 'Howaldt',
        'praxis_kuerzel': 'HW',
        'where_str': "SUBSTR(number, 1, 2) = 'HW' OR SUBSTR(number, 1, 5) = 'G6303'",
        'usergroup': 1,
        'fcid_import_border': 2025081823595900,
        'muid': -1 
    },
    'Naumann': {
        'name': 'Dr. Axel Naumann',
        'praxis_kuerzel': 'AN',
        'where_str': "SUBSTR(number, 1, 2) = 'AN'",
        'usergroup': 3,
        'fcid_import_border': 2025081823595900,
        'muid': -3 
    },
    'Mross': {
        'name': 'Dr. med. Michael R. Mroß',
        'praxis_kuerzel': 'DM',
        'where_str': "SUBSTR(number, 1, 2) = 'DM' OR SUBSTR(number, 1, 5) = 'G9862'",
        'usergroup': 4,
        'fcid_import_border': 2025081823595900,
        'muid': -4 
    },
    'eugastro': {
        'name': 'eugastro GmbH, Prof. Schiefke',
        'praxis_kuerzel': 'EU',
        'where_str': "SUBSTR(number, 1, 2) = 'EU'",
        'usergroup': 5,
        'fcid_import_border': 2025081823595900,
        'muid': -5 
    },
    'psdocs': {
        'name': 'psdocs Dr. Funda, Pirmasens',
        'praxis_kuerzel': 'PS',
        'where_str': "SUBSTR(number, 1, 2) = 'PS'",
        'usergroup': 6,
        'fcid_import_border': 2025081823595900,
        'muid': -6 
    },
    'Landry': {
        'name': 'Dr. Wilfred Landry, MVZ Dachau',
        'praxis_kuerzel': 'WL',
        'where_str': "SUBSTR(number, 1, 2) = 'WL'",
        'usergroup': 7,
        'fcid_import_border': 2025081823595900,
        'muid': -7 
    },
    'Ochsenkuehn': {
        'name': 'Prof. Dr. med. Thomas Ochsenkühn',
        'praxis_kuerzel': 'TO',
        'where_str': "SUBSTR(number, 1, 2) = 'TO' OR SUBSTR(number, 1, 5) = 'G4299'",
        'usergroup': 8,
        'fcid_import_border': 2025081823595900,
        'muid': -8 
    },
    'Marienhospital': {
        'name': 'St. Marienhospital Vechta',
        'praxis_kuerzel': 'MV',
        'where_str': "SUBSTR(number, 1, 2) = 'MV'",
        'usergroup': 9,
        'fcid_import_border': 2025081823595900,
        'muid': -9 
    }
    # TH Test
}

# MANUELL: CEDUR Nummer HW-195538, alte Praxis ID:  11267.
# Bitte ändern in neue Praxis ID:  20730 (fcid 2019112113371500)
# muid 2025070711332139

# this_praxis = praxis_a['Howaldt']           # 3
# this_praxis = praxis_a['Naumann']           # 3
# this_praxis = praxis_a['Marienhospital']    # 9
# this_praxis = praxis_a['psdocs']            # 6
# this_praxis = praxis_a['eugastro']          # 5
# this_praxis = praxis_a['Landry']            # 7
# this_praxis = praxis_a['Mross']             # 4
# this_praxis = praxis_a['Ochsenkuehn']       # 8 #  GROSSE PROBLEME WEGEN DOPPELTEN CREATE-IDs
print(this_praxis)


{'name': 'Prof. Dr. med. Thomas Ochsenkühn', 'praxis_kuerzel': 'TO', 'where_str': "SUBSTR(number, 1, 2) = 'TO' OR SUBSTR(number, 1, 5) = 'G4299'", 'usergroup': 8, 'fcid_import_border': 2025081823595900, 'muid': -8}


In [67]:

# ONLY RE-IMPORT OR SECOND IMPORT
# SELECT * FROM forms_10003 WHERE fcid>2025081823595900 59 7
# SELECT * FROM forms_10005 WHERE fcid>2025081823595900 980 98 
# SELECT * FROM forms_10010 WHERE fcid>2025081823595900 3878 94
# cursor.execute("DELETE FROM forms_10003 WHERE usergroup=" + str(praxis_a['Howaldt']['usergroup']) + " AND fcid<=" + str(praxis_a['Howaldt']['fcid_import_border']))
# cursor.execute("DELETE FROM forms_10005 WHERE usergroup=" + str(praxis_a['Howaldt']['usergroup']) + " AND fcid<=" + str(praxis_a['Howaldt']['fcid_import_border']))
# cursor.execute("DELETE FROM forms_10010 WHERE usergroup=" + str(praxis_a['Howaldt']['usergroup']) + " AND fcid<=" + str(praxis_a['Howaldt']['fcid_import_border']))
# conn.commit()
# print(f"Cedur 3 for {this_praxis['name']} deleted")

In [68]:
# import patients
print(f"Cedur 3 patients for {this_praxis['name']} start patients import")

check_if_fcid_exists = {}
cursor.execute("SELECT DISTINCT fcid FROM forms_10003")
conn.commit()
rows = cursor.fetchall()
results_as_dicts = [dict(row) for row in rows]
for row_dict in results_as_dicts:
    check_if_fcid_exists[row_dict['fcid']] = True
print(check_if_fcid_exists)

import_patient_base(this_praxis, check_if_fcid_exists)

Cedur 3 patients for Prof. Dr. med. Thomas Ochsenkühn start patients import
{2013010715082300: True, 2013040209423100: True, 2013060620351600: True, 2013071513131500: True, 2013071513344100: True, 2013071514040400: True, 2013071609030100: True, 2013071609181200: True, 2013071609511300: True, 2013071610164400: True, 2013071610190400: True, 2013071612125600: True, 2013071612174300: True, 2013071612273700: True, 2013071612395700: True, 2013071612432100: True, 2013071613055800: True, 2013071613182400: True, 2013071714413800: True, 2013071809204300: True, 2013071809241100: True, 2013071809292700: True, 2013071810110500: True, 2013071810135300: True, 2013071810211600: True, 2013071810262100: True, 2013071811033400: True, 2013071811092400: True, 2013071811121300: True, 2013071811261500: True, 2013071811572500: True, 2013071812002900: True, 2013071812042200: True, 2013071812112300: True, 2013071812325100: True, 2013071812370000: True, 2013071812573600: True, 2013071910445000: True, 20130719104

100 200 2020060718062700 schon vorhanden, erhöhe um 1
2020060718062700 schon vorhanden, erhöhe um 1
2020060718062701 schon vorhanden, erhöhe um 1
2020060718062700 schon vorhanden, erhöhe um 1
2020060718062701 schon vorhanden, erhöhe um 1
2020060718062702 schon vorhanden, erhöhe um 1
300 2020060718062700 schon vorhanden, erhöhe um 1
2020060718062701 schon vorhanden, erhöhe um 1
2020060718062702 schon vorhanden, erhöhe um 1
2020060718062703 schon vorhanden, erhöhe um 1
2020060718062700 schon vorhanden, erhöhe um 1
2020060718062701 schon vorhanden, erhöhe um 1
2020060718062702 schon vorhanden, erhöhe um 1
2020060718062703 schon vorhanden, erhöhe um 1
2020060718062704 schon vorhanden, erhöhe um 1
2020060718062800 schon vorhanden, erhöhe um 1
2020060718062700 schon vorhanden, erhöhe um 1
2020060718062701 schon vorhanden, erhöhe um 1
2020060718062702 schon vorhanden, erhöhe um 1
2020060718062703 schon vorhanden, erhöhe um 1
2020060718062704 schon vorhanden, erhöhe um 1
2020060718062705 schon

In [69]:

# MAIN

# cursor.execute("DELETE FROM forms_10010 WHERE fcid=2025010900302727")
# conn.commit()
# patient_list_a = [2024072408540900]
patient_list_a = get_patient_list_a(this_praxis)
print(f"  Patients: {len(patient_list_a)}")


def get_cedur_data_allgemein(pid, visite_a):

    def weitere_erkrakungen(field):
        # print("FIELD_:" + field)
        if field == "weitereErkrankungen":
            val = "Ja"
        if field == "weitereErkrankungen_0":
            val = "Akne inversa"
        if field == "weitereErkrankungen_1":
            val = "Asthma bronchiale"
        if field == "weitereErkrankungen_2":
            val = "Bauchspeicheldrüsenkrebs"
        if field == "weitereErkrankungen_3":
            val = "Blasenentzündung"
        if field == "weitereErkrankungen_4":
            val = "Bluthochdruck"
        if field == "weitereErkrankungen_5":
            val = "Brustkrebs"
        if field == "weitereErkrankungen_7":
            val = "Darmkrebs"
        if field == "weitereErkrankungen_8":
            val = "Diabetes mellitus"
        if field == "weitereErkrankungen_9":
            val = "Depression"
        if field == "weitereErkrankungen_10":
            val = "Eierstock-Krebs"
        if field == "weitereErkrankungen_11":
            val = "Fatigue Syndrom (ständige Müdigkeit, Abgeschlagenheit)"
        if field == "weitereErkrankungen_12":
            val = "Fettstoffwechselstörung"
        if field == "weitereErkrankungen_13":
            val = "Gallensteine"
        if field == "weitereErkrankungen_14":
            val = "Grauer Star"
        if field == "weitereErkrankungen_15":
            val = "Grüner Star"
        if field == "weitereErkrankungen_16":
            val = "Gürtelrose (Herpes zoster)"
        if field == "weitereErkrankungen_17":
            val = "Hautkrebs (schwarzer und weißer Hautkrebs)"
        if field == "weitereErkrankungen_18":
            val = "Haarausfall"
        if field == "weitereErkrankungen_19":
            val = "Hepatitis (A, B, C, D oder E)"
        if field == "weitereErkrankungen_20":
            val = "Herzinfarkt"
        if field == "weitereErkrankungen_21":
            val = "Hodenkrebs"
        if field == "weitereErkrankungen_22":
            val = "HIV"
        if field == "weitereErkrankungen_23":
            val = "Koronare Herzkrankheit"
        if field == "weitereErkrankungen_24":
            val = "Kurzdarmsyndrom"
        if field == "weitereErkrankungen_25":
            val = "Leberzirrhose"
        if field == "weitereErkrankungen_26":
            val = "Leukämie"
        if field == "weitereErkrankungen_27":
            val = "Lungenkrebs"
        if field == "weitereErkrankungen_28":
            val = "Lymphdrüsenkrebs"
        if field == "weitereErkrankungen_29":
            val = "Migräne"
        if field == "weitereErkrankungen_30":
            val = "Multiple Sklerose (MS)"
        if field == "weitereErkrankungen_31":
            val = "Nierenerkrankung"
        if field == "weitereErkrankungen_32":
            val = "Nierensteine"
        if field == "weitereErkrankungen_33":
            val = "Osteoporose"
        if field == "weitereErkrankungen_34":
            val = "PBC (Primär biliäre Zirrhose / Cholangitis)"
        if field == "weitereErkrankungen_35":
            val = "Prostatakrebs"
        if field == "weitereErkrankungen_36":
            val = "PSC (primär)"
        if field == "weitereErkrankungen_37":
            val = "Rheumatoide Arthritis"
        if field == "weitereErkrankungen_38":
            val = "Schilddrüsenüberfunktion"
        if field == "weitereErkrankungen_39":
            val = "Schilddrüsenunterfunktion"
        if field == "weitereErkrankungen_40":
            val = "Schlafstörungen"
        if field == "weitereErkrankungen_41":
            val = "Schuppenflechte"
        if field == "weitereErkrankungen_42":
            val = "Thrombose"
        return val

    def update_SESCD(visite_a, visite_fcid, ses_cd1_dict, a0, a1, a2, a3):
        mappings = {
            'ulzeration': {
                0: 'keine',
                1: 'aphtoid < 0,5cm',
                2: '0,5cm - 2cm',
                3: '> 2cm'
            },
            'ausdehnung_ulzeration': {
                0: 'keine',
                1: '< 10%',
                2: '10 - 30%',
                3: '> 30%'
            },
            'entzuendete_oberflaeche': {
                0: 'keine',
                1: '< 50%',
                2: '50 - 75%',
                3: '> 75%'
            },
            'stenose': {
                0: 'keine',
                1: 'singulär, passierbar',
                2: 'multipel, passierbar',
                3: 'nicht passierbar'
            }
        }

        # Keys mit den passenden a-Werten verknüpfen
        key_to_a = {
            'ulzeration': a0,
            'ausdehnung_ulzeration': a1,
            'entzuendete_oberflaeche': a2,
            'stenose': a3
        }

        for key, fid in key_to_a.items():
            value = ses_cd1_dict.get(key)
            if value in mappings[key]:
                visite_a[visite_fcid][fid] = mappings[key][value]

    conform_replace = { # beim Einlesen
        102600: ' cm',
        102700: ' kg',
        103500: ' unit',
        110200: ' %',
        106300: ' Tage',
        110600: ' g/dl',
        110700: ' ng/ml',
        111100: ' g/l',
        110500: ' mg/kg',
        106600: ' Std.',
        102500: ' Tage'
    }

    show_details = 0
    rows = get_rows_from_cedur('CEDUR3_allgemein', pid)
    results_as_dicts = [dict(row) for row in rows]
    # print(results_as_dicts)
    for row_dict in results_as_dicts:
        weitereErkankungen_sammler = []
        visite_fcid = fcid_a[row_dict['cid']]
        if visite_fcid not in visite_a:
            visite_a[visite_fcid] = {}
        print(f"------ Visite: {visite_fcid} -----")
        for column_name, value in row_dict.items():
            if "@base64-textarea:" in str(value): 
                base64_str = str(value).removeprefix("@base64-textarea:")
                base46_str_decoded = base64.b64decode(base64_str)
                base46_str_decoded_str = base46_str_decoded.decode('utf-8')
                # print("BASE_found:" + base46_str_decoded_str)
                value = base46_str_decoded_str
            if "@base64-json:" in str(value): 
                base64_str = str(value).removeprefix("@base64-json:")
                base46_str_decoded = base64.b64decode(base64_str)
                base46_str_decoded_str = base46_str_decoded.decode('utf-8')
                # print("BASE_found:" + base46_str_decoded_str)
                value = base46_str_decoded_str
            if column_name in cedur2miq_a:
                if value != None and value != '':
                    # Werte die einen Schlüssel in forms_definition haben
                    
                    # Spezielle Anpassungen Labor
                    if (cedur2miq_a[column_name] == 110600):
                        parts = value.split(' ')
                        value = parts[0]
                        if len(parts) > 1:
                            haemo_unit = parts[1]
                            visite_a[visite_fcid][110602] = haemo_unit
                        else:
                            haemo_unit = None
                    
                    # Cleaning Daten (also z.b. auch Entfernung der Einheiten aus Labor)
                    value = clean_replace(cedur2miq_a[column_name], conform_replace, value);
                    visite_a[visite_fcid][cedur2miq_a[column_name]] = value

                    # Spezielle Anpassungen Labor SES
                    if (cedur2miq_a[column_name] == 116208):
                        ses_cd1_dict = json.loads(value)
                        update_SESCD(visite_a, visite_fcid, ses_cd1_dict, 116202, 116204, 116206, 116208)
                        print(f" OK SES ileum: {visite_a[visite_fcid][116202],visite_a[visite_fcid][116204],visite_a[visite_fcid][116206],visite_a[visite_fcid][116208]}")
                    if (cedur2miq_a[column_name] == 116308):
                        ses_cd2_dict = json.loads(value)
                        update_SESCD(visite_a, visite_fcid, ses_cd2_dict, 116302, 116304, 116306, 116308)
                        print(f" OK SES Colon rechts: {visite_a[visite_fcid][116302],visite_a[visite_fcid][116304],visite_a[visite_fcid][116306],visite_a[visite_fcid][116308]}")
                    if (cedur2miq_a[column_name] == 116408):
                        ses_cd3_dict = json.loads(value)
                        update_SESCD(visite_a, visite_fcid, ses_cd3_dict, 116402, 116404, 116406, 116408)
                        print(f" OK SES Colon transversum: {visite_a[visite_fcid][116402],visite_a[visite_fcid][116404],visite_a[visite_fcid][116406],visite_a[visite_fcid][116408]}")
                    if (cedur2miq_a[column_name] == 116508):
                        ses_cd4_dict = json.loads(value)
                        update_SESCD(visite_a, visite_fcid, ses_cd4_dict, 116502, 116504, 116506, 116508)
                        print(f" OK SES Colon links: {visite_a[visite_fcid][116502],visite_a[visite_fcid][116504],visite_a[visite_fcid][116506],visite_a[visite_fcid][116508]}")
                    if (cedur2miq_a[column_name] == 116608):
                        ses_cd5_dict = json.loads(value)
                        update_SESCD(visite_a, visite_fcid, ses_cd5_dict, 116602, 116604, 116606, 116608)
                        print(f" OK SES Rektum: {visite_a[visite_fcid][116602],visite_a[visite_fcid][116604],visite_a[visite_fcid][116606],visite_a[visite_fcid][116608]}")

                    # Ausgabe der tatsächlichen Inhalte    
                    print(f" OK: {column_name} =  {cedur2miq_a[column_name]}: {value}")
                
                else: 
                    if show_details:
                        print(f"    leer: {column_name}")    
            elif "weitereErkrankungen" in column_name:
                # print("VAL:" + str(value))
                if value=='Ja':
                    weitereErkankungen_sammler.append(weitere_erkrakungen(column_name))      
            elif "CDAI012_haben_oder_hatten" in column_name:
                if value == 'Nein':
                    visite_a[visite_fcid][104200] = 'Nein'
                    visite_a[visite_fcid][104500] = 'Nein'
                    print(f" OK: {column_name} =  104200, 104500: {value}")
                    # sys.exit()
            else: 
                if show_details:
                    print(f"    Schlüssel fehlt: {column_name} = {correct_coding(value)}")
                if column_name == 'Montreal_Lokalisation_Crohn' and value:
                        parts = correct_coding(value).split('|')
                        for loc in parts:
                            if loc == 'Nur terminales Ileum':
                                visite_a[visite_fcid][101902] = 1
                            elif loc == 'Nur Colon':
                                visite_a[visite_fcid][101904] = 1
                            if loc == 'Nur terminales Ileum':
                                visite_a[visite_fcid][101902] = 1
                            if loc == 'Ileo-Colon':
                                visite_a[visite_fcid][101906] = 1
                            if loc == 'Oberer GI-Trakt (Öspohagus u./o. Magen u./o. Duodenum)':
                                visite_a[visite_fcid][101908] = 1
                            if loc == 'Dünndarmbefall (Jejunum / Ileum (außer term. Ileum)':
                                visite_a[visite_fcid][101910] = 1    
        visite_a[visite_fcid][111301] = ",".join(weitereErkankungen_sammler)
        if visite_a[visite_fcid][111301]:
            print(f" OK: Diverse weitereErkrankungen_ =  111301: {visite_a[visite_fcid][111301]}")
    return visite_a

def get_cedur_data_lebensqualitaet(pid, visite_a):
    show_details = 0
    rows = get_rows_from_cedur('CEDUR3_lebensqualitaet', pid)
    results_as_dicts = [dict(row) for row in rows]
    # print(results_as_dicts)
    for row_dict in results_as_dicts:
        visite_fcid = fcid_a[row_dict['cid']]
        if visite_fcid not in visite_a:
            visite_a[visite_fcid] = {}
        print(f"------ {visite_fcid} -----")
        for column_name, value in row_dict.items():
            if "@base64-textarea:" in str(value): 
                base64_str = str(value).removeprefix("@base64-textarea:")
                base46_str_decoded = base64.b64decode(base64_str)
                base46_str_decoded_str = base46_str_decoded.decode('utf-8')
                # print("BASE_found:" + base46_str_decoded_str)
                value = base46_str_decoded_str
            if "@base64-json:" in str(value): 
                base64_str = str(value).removeprefix("@base64-json:")
                base46_str_decoded = base64.b64decode(base64_str)
                base46_str_decoded_str = base46_str_decoded.decode('utf-8')
                # print("BASE_found:" + base46_str_decoded_str)
                value = base46_str_decoded_str
            if column_name in cedur2miq_a:
                if value != None and value != '':
                    value = clean_replace(cedur2miq_a[column_name], {}, value);
                    # print(f"{column_name} =  {cedur2miq_a[column_name]}: {value}")
                    visite_a[visite_fcid][cedur2miq_a[column_name]] = value
                else: 
                    if show_details:
                        print(f"    leer: {column_name}")    
            else: 
                if show_details:
                    print(f"    Schlüssel fehlt: {column_name} = {correct_coding(value)}")
    return visite_a

for miq_pid in patient_list_a:
    patient_a = get_patient_data(miq_pid)        
    cedur_pid = patient_a[102]
    patient_a.pop(102, None)
    patient_a[90] = miq_pid
    print(f" Import {miq_pid}: {patient_a[90]}") 
    visite_a = {}
    visite_a = get_cedur_data_allgemein(cedur_pid, visite_a) 
    visite_a = get_cedur_data_lebensqualitaet(cedur_pid, visite_a)      
    # print(visite_a)
    for fcid_visite, daten_dict in visite_a.items():
        patient_a[93] = fcid_visite
        first_visit = 0 # TODO
        patient_a[94] = first_visit
        groesse = 0 # TODO
        patient_a[97] = groesse
        add_patient_base_data(10005, fcid_visite, patient_a)
        visit_date = str(fcid_visite)
        visit_date = visit_date[0:4] + '-' + visit_date[4:6]  + '-' + visit_date[6:8]  
        query = build_query_str(10005, fcid_visite, 10005020, visit_date, this_praxis['muid'], this_praxis['usergroup'])
        cursor.execute(query)
        conn.commit()
        print(f"--- Visite-ID: {fcid_visite} ---")
        add_patient_base_data(10010, fcid_visite, patient_a)
        for fid, fcont in daten_dict.items():
            if (fcont == 'nein'):
                fcont = 'Nein'
            if fid in [102200,102300,106400,107100,107400,107700,108000,108300] and fcont!='':
                fcont = format_date(fcont)
            if fid == 106600:
                std = int(fcont)
                if std < 20:
                    fcont = "Teilzeit II (bis 20h)"
                elif std < 31:
                    fcont = "Teilzeit I (21h-30h)"
                else:
                    fcont = "Vollzeit (>30h)"
            if fid in [106300, 102500] and fcont!='':
                # wenn nicht x TAGE:
                if "|" in fcont:
                    fcont = len(fcont.split("|"))
                elif "-" in fcont:
                    fcont = 1
            if fid == 115500:
                fcont = fcont.replace('|', ',').replace("'", '').replace('"', '')
            print(f"I:  fid: {fid}, fcont: '{fcont}'")
            query = build_query_str(10010, fcid_visite, fid, fcont, this_praxis['muid'], this_praxis['usergroup'])
            cursor.execute(query)
        conn.commit()
    


  Patients: 443
 Import 2013061909133200: 2013061909133200
------ Visite: 2014062200224327 -----
 OK: CDAI001 =  95: Morbus Crohn
 OK: CDAI003 =  102400: Nein
 OK: CDAI_Size =  102600: 164
 OK: CDAI006 =  102700: 70
 OK: Raucher =  102800: Nein
 OK: menge_zigarette =  103400: 0-5
 OK: CDAI009 =  103500: 0
 OK: CDAI014 =  103600: kein Blut
 OK: CDAI010 =  103900: mäßige
 OK: CDAI011 =  104000: beeinträchtigt
 OK: CDAI012 =  104200: Nein
 OK: fist_and =  104400: Nein
 OK: taetigkeit =  106000: Angestellt tätig
 OK: Fehltage =  106300: 10
 OK: labor_hct =  110200: 39
 OK: eim_auge =  115600: Nein
 OK: eim_temp =  115700: Nein
 OK: eim_haut =  115800: Nein
 OK: eim_gelenk =  115900: Nein
------ Visite: 2014030600225099 -----
 OK: CDAI001 =  95: Morbus Crohn
 OK: CDAI003 =  102400: Nein
 OK: CDAI_Size =  102600: 164
 OK: CDAI006 =  102700: 67
 OK: Raucher =  102800: Nein
 OK: menge_zigarette =  103400: 0-5
 OK: CDAI009 =  103500: 0
 OK: CDAI014 =  103600: kein Blut
 OK: CDAI010 =  103900: m

In [70]:

cursor.close()
conn.close()

# UPDATE forms_10010 SET fcont='Rentner' WHERE fid=106000 AND fcont='Rentner*in';
# UPDATE forms_10010 SET fcont='Rentner (reguläre Altersrente)' WHERE fid=106000 AND fcont='Rentner';
# UPDATE forms_10010 SET fcont='Student / Schüler / in Ausbildung' WHERE fid=106000 AND fcont='Student*in / Schüler*in / in Ausbildung';
# UPDATE forms_10010 SET fcont='Rentner (aufgrund CED Erkrankung)' WHERE fid=106000 AND fcont='Berentet aufgrund CED';
# UPDATE forms_10010 SET fcont='Rentner (aufgrund anderer Erkrankungen)' WHERE fid=106000 AND fcont='Berentet aufgrund anderer Erkrankungen';
# UPDATE forms_10010 SET fcont='Rentner (reguläre Altersrente)' WHERE fid=106000 AND fcont='Rentner*in';
# UPDATE forms_10010 SET fcont='Hauptschulabschluß' WHERE fid=106700 AND fcont='Hauptschule';


